In [1]:
import numpy as np
import os
import pandas as pd

import torch
import torch.nn as nn

import tensorflow as tf

2023-01-16 16:55:46.175474: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-01-16 16:55:47.119885: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2023-01-16 16:55:47.119965: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2023-01-16 16:55:47.119985: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like t

In [2]:
data_folder = "/work/bd/summer2022/insample/datacache"
dailydata = os.path.join(data_folder, 'dailydata') # close, high, low, open, return, tvrvalue, tvrvolume.parquet
labeldata = os.path.join(data_folder, 'labeldata') # 
univdata = os.path.join(data_folder, 'univdata')
xmindata = os.path.join(data_folder, 'xmindata')

In [3]:
df_close = pd.read_parquet(os.path.join(dailydata, 'close.parquet'))
df_high = pd.read_parquet(os.path.join(dailydata, 'high.parquet'))
df_low = pd.read_parquet(os.path.join(dailydata, 'low.parquet'))
df_open = pd.read_parquet(os.path.join(dailydata, 'open.parquet'))
df_tvrvalue = pd.read_parquet(os.path.join(dailydata, 'tvrvalue.parquet'))
df_tvrvolume = pd.read_parquet(os.path.join(dailydata, 'tvrvolume.parquet'))

df_return = pd.read_parquet(os.path.join(dailydata, 'return.parquet'))

In [4]:
df_m_high = pd.read_parquet(os.path.join(xmindata, 'totaltradeshare.parquet'))
df_m_high

000001       000002  000003     000004     000005  \
date     time                                                                
20180102 93000000      862284.0     185545.0     0.0      800.0     9800.0   
         100000000   67416917.0   28971585.0     0.0   111000.0   627124.0   
         103000000  102305841.0   39134827.0     0.0   164600.0  1013228.0   
         110000000  129035550.0   42674082.0     0.0   225300.0  1077128.0   
         130000000  141316052.0   45710942.0     0.0   284800.0  1287724.0   
...                         ...          ...     ...        ...        ...   
20211231 130000000   76918711.0   46143019.0     0.0   975700.0  5862407.0   
         133000000  105985199.0   84210528.0     0.0  1106500.0  6948507.0   
         140000000  126817081.0   96299421.0     0.0  1295000.0  7190407.0   
         143000000  149847173.0  102635117.0     0.0  1425800.0  7721707.0   
         150000000  175076089.0  115918655.0     0.0  1674400.0  9534527.0   

                        000006     000007       000008      000009     000010  \
date     time                                                                   
20180102 93000000          0.0        0.0      33600.0    105000.0     8400.0   
         100000000         0.0        0.0    2006600.0   3568557.0  1506910.0   
         103000000         0.0        0.0    2646100.0   6252287.0  2100910.0   
         110000000         0.0        0.0    3166300.0   9419237.0  2681710.0   
         130000000         0.0        0.0    3682200.0  10907497.0  4842111.0   
...                        ...        ...          ...         ...        ...   
20211231 130000000   4949104.0  6165986.0  195854353.0  48387621.0  5403800.0   
         133000000   9458020.0  7800686.0  204305453.0  52108373.0  5644575.0   
         140000000  10122524.0  8468986.0  212073594.0  56764012.0  6087675.0   
         143000000  11095024.0  9135186.0  219999253.0  61229416.0  6358875.0   
         150000000  12291425.0  9947136.0  235181963.0  69648325.0  7111675.0   

                    ...    688786    688787    688788    688789    688793  \
date     time       ...                                                     
20180102 93000000   ...       0.0       0.0       0.0       0.0       0.0   
         100000000  ...       0.0       0.0       0.0       0.0       0.0   
         103000000  ...       0.0       0.0       0.0       0.0       0.0   
         110000000  ...       0.0       0.0       0.0       0.0       0.0   
         130000000  ...       0.0       0.0       0.0       0.0       0.0   
...                 ...       ...       ...       ...       ...       ...   
20211231 130000000  ...  243344.0  642643.0  373217.0  125343.0  587838.0   
         133000000  ...  269541.0  751890.0  424745.0  146763.0  653556.0   
         140000000  ...  291548.0  786154.0  467633.0  178402.0  818635.0   
         143000000  ...  338652.0  880697.0  539970.0  195608.0  892443.0   
         150000000  ...  418519.0  994823.0  590372.0  215007.0  930053.0   

                      688798     688799    688800     688819      688981  
date     time                                                             
20180102 93000000        0.0        0.0       0.0        0.0         0.0  
         100000000       0.0        0.0       0.0        0.0         0.0  
         103000000       0.0        0.0       0.0        0.0         0.0  
         110000000       0.0        0.0       0.0        0.0         0.0  
         130000000       0.0        0.0       0.0        0.0         0.0  
...                      ...        ...       ...        ...         ...  
20211231 130000000  141391.0   911667.0  418363.0   867405.0   8267035.0  
         133000000  308022.0  1226167.0  490116.0  1025973.0   9460315.0  
         140000000  386627.0  1312251.0  542159.0  1204479.0  10651817.0  
         143000000  493028.0  1403594.0  647958.0  1326525.0  12055480.0  
         150000000  536529.0  1587397.0  740989.0  152

In [7]:
df_tvrvolume

000001       000002  000003     000004      000005      000006  \
date                                                                            
20180102  208159248.0   68343352.0     0.0   626181.0   7153934.5         0.0   
20180103  296249856.0   64687020.0     0.0  1879539.0   6799065.0         0.0   
20180104  185450944.0   52908580.0     0.0  1454066.0   4380978.0         0.0   
20180105  121031272.0   84310192.0     0.0  1044404.0   8522627.0         0.0   
20180108  215862080.0   83078360.0     0.0   717585.0   6872269.0         0.0   
...               ...          ...     ...        ...         ...         ...   
20211227   73111904.0   75474416.0     0.0  1729558.0   5285707.0   9452689.0   
20211228  112663888.0   69046784.0     0.0  4626402.0   8552560.0   8862624.0   
20211229  146937408.0   58214420.0     0.0  2215562.0  10282406.0   6209640.0   
20211230   79666360.0   81221296.0     0.0  2450900.0   9352639.0   7604085.0   
20211231  175076080.0  115918648.0     0.0  1674400.0   9534527.0  12291425.0   

             000007       000008      000009      000010  ...        688786  \
date                                                      ...                 
20180102        0.0    8289999.0  19269994.0   8519811.0  ...       0.00000   
20180103        0.0    7000622.0  23092096.0  11296264.0  ...       0.00000   
20180104        0.0    7626333.0  46992708.0   9369600.0  ...       0.00000   
20180105        0.0    8327572.5  25990264.0  14633138.0  ...       0.00000   
20180108        0.0    4981915.0  23703432.0  40269504.0  ...       0.00000   
...             ...          ...         ...         ...  ...           ...   
20211227  9585444.0  313267968.0  62756712.0   4881800.0  ...  303384.00000   
20211228  6988400.0  210091168.0  82109448.0   4030004.0  ...  265227.00000   
20211229  6511555.0  138599632.0  68111984.0   4672004.0  ...  451245.03125   
20211230  6951200.0  170631056.0  68369672.0   4665781.0  ...  795714.00000   
20211231  9947136.0  235181968.0  69648328.0   7111675.0  ...  418519.00000   

               688787        688788         688789    688793    688798  \
date                                                                     
20180102       0.0000       0.00000       0.000000       0.0       0.0   
20180103       0.0000       0.00000       0.000000       0.0       0.0   
20180104       0.0000       0.00000       0.000000       0.0       0.0   
20180105       0.0000       0.00000       0.000000       0.0       0.0   
20180108       0.0000       0.00000       0.000000       0.0       0.0   
...               ...           ...            ...       ...       ...   
20211227  501423.0000  452313.00000  223338.984375  644708.0  309409.0   
20211228  504589.0000  290295.00000  116365.000000  724657.0  384539.0   
20211229  692136.0000  494831.96875  183905.000000  509209.0  418127.0   
20211230  408683.0000  403014.00000  163061.000000  606685.0  403798.0   
20211231  994823.0625  590372.00000  215007.000000  930053.0  536529.0   

                688799    688800     688819      688981  
date                                                     
20180102  0.000000e+00       0.0        0.0         0.0  
20180103  0.000000e+00       0.0        0.0         0.0  
20180104  0.000000e+00       0.0        0.0         0.0  
20180105  0.000000e+00       0.0        0.0         0.0  
20180108  0.000000e+00       0.0        0.0         0.0  
...                ...       ...        ...         ...  
20211227  1.852969e+06  602970.0  1307597.0  10306999.0  
20211228  8.945731e+05  307456.0  1506287.0  12549961.0  
20211229  1.186025e+06  732254.0  1025163.0  11656150.0  
20211230  8.919870e+05  549155.0  1443660.0  15721509.0  
20211231  1.587397e+06  740989.0  1525722.0  14307270.0  

[973 rows x 5044 columns]

In [5]:
df_y0 = pd.read_parquet(os.path.join(labeldata, 'Y_0.parquet'))

In [13]:
loss = nn.CrossEntropyLoss(reduction='none')
input = torch.softmax(torch.randn(3, 5), dim=1)
target = torch.zeros(3, 5)
target[:, 0] = 1
loss(input, target)

tensor([1.6903, 1.6456, 1.6452])

In [6]:
from data import TrainValData, TimeSeriesData

In [7]:
features = [df_open, df_high, df_low, df_tvrvalue, df_tvrvolume, df_close]
stock_data_list = []

stocks = df_open.columns.values
for stock in stocks:
    one_stock_features = []
    for feature in features:
        one_stock_features.append(feature[stock].values[:-2].reshape(-1, 1))
    stock_np_features = np.concatenate(one_stock_features, axis=1)
    dates = feature.index.values[:-2]
    labels = df_y0[stock].values[1:]
    print(stock_np_features.shape, dates.shape, labels.shape)
    stock_data_list.append(TimeSeriesData(dates=dates, data=stock_np_features, labels=labels))
print(len(stocks))


(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (971,) (971,)
(971, 6) (9

In [7]:
np.isnan(stock_data_list[5000].data)

array([[ True,  True,  True, False, False,  True],
       [ True,  True,  True, False, False,  True],
       [ True,  True,  True, False, False,  True],
       ...,
       [False, False, False, False, False, False],
       [False, False, False, False, False, False],
       [False, False, False, False, False, False]])

In [18]:
train_val_data = TrainValData(time_series_list=stock_data_list, train_length=800, validate_length=150, history_length=10)
train, val, dates_info = train_val_data.get(20180102, order='by_date')

data_all shape: (378300, 6, 10)
label_all shape: (378300,)
dates_series_all shape: (378300, 2)


TypeError: torch._VariableFunctionsClass.from_numpy() takes no keyword arguments

In [8]:
np.isnan(np.array(stock_data_list[5000].labels[0]))

True

In [7]:
import torch
import torch.nn as nn


class StockDataset(torch.utils.data.Dataset):
    def __init__(self, stock_list, history_length=20, stride=10) -> None:
        super().__init__()
        self.stock_list = stock_list
        self.history_length = history_length
        self.stride = stride
        self.length = len(stock_list[0].dates)
        self.max_inner_idx = (self.length - self.history_length) // self.stride
    
    def __getitem__(self, index):
        stock_id =  index // self.max_inner_idx#(index * self.stride + self.history_length) // self.length
        inner_stock_idx = index - stock_id * self.max_inner_idx
        # print(stock_id, inner_stock_idx)
        try:
            feature = self.stock_list[stock_id].data[inner_stock_idx*self.stride: inner_stock_idx*self.stride+self.history_length]
        except:
            print(stock_id)
        label = self.stock_list[stock_id].labels[inner_stock_idx*self.stride+self.history_length-1]

        return feature, label

    def __len__(self):
        return (self.max_inner_idx) * len(self.stock_list)

sd = StockDataset(stock_data_list)

In [8]:
def my_collate(batch):
    # print(len(batch))
    batch_feat = []
    batch_label = []
    for item in batch:
        # print(item)
        # print(True in np.isnan(item[0]))
        # print((True == np.isnan(np.array(item[1]))))
        if (True in np.isnan(item[0])) or (True == np.isnan(np.array(item[1]))):
            pass
        else:
            batch_feat.append(torch.from_numpy(item[0]).unsqueeze(0))
            batch_label.append(torch.tensor(item[1]))
    if len(batch_feat) > 0:
        feats = torch.cat(batch_feat, dim=0)
        labels = torch.tensor(batch_label)
        return feats, labels
    return None, None

dataloader = torch.utils.data.DataLoader(sd, batch_size=128,shuffle=True, collate_fn=my_collate)

In [36]:

for feat, label in dataloader:
    if feat != None:
        output = model(feat)

        # if feat.shape[0] != 128:
        #     print(feat.shape)
    # print(label.shape)


torch.Size([2970])
torch.Size([5940])
tensor([[[-0.3880, -0.3542, -0.3764,  ...,  0.6908,  1.2043,  1.2671],
         [-0.3316, -0.3077, -0.3313,  ...,  0.0309,  0.7780,  0.8218]],

        [[-0.4084, -0.3766, -0.4086,  ...,  0.5116, -0.4886, -0.4202],
         [-0.4179, -0.3833, -0.4144,  ..., -0.4296, -0.2848, -0.1839]],

        [[-0.3731, -0.3606, -0.3967,  ..., -1.0670, -1.8265, -1.6998],
         [-0.3685, -0.3376, -0.3668,  ...,  0.8446,  0.4005,  0.2468]],

        ...,

        [[-0.3378, -0.3245, -0.3317,  ...,  0.2926, -0.3143, -0.3224],
         [-0.3053, -0.3371, -0.3294,  ..., -1.8914, -0.3070, -0.2525]],

        [[ 1.2130,  1.0306,  1.1062,  ...,  0.8662,  0.9186,  0.9385],
         [ 0.8680,  0.5639,  0.8284,  ...,  0.0327,  0.1818,  0.1369]],

        [[-0.3664, -0.3405, -0.3643,  ...,  0.4610, -1.8776, -1.8305],
         [-0.1104, -0.0408, -0.0732,  ...,  0.8355,  1.4134,  1.4381]]],
       grad_fn=<TransposeBackward0>) torch.Size([99, 2, 54])
torch.Size([3120])
torc

In [14]:
a = torch.randn(1, 2, 3, 4)
stda = torch.std(a, dim=-2)
print(stda, stda.shape)

tensor([[[0.7095, 0.8552, 1.5340, 0.7352],
         [1.4623, 1.5250, 1.1155, 0.2358]]]) torch.Size([1, 2, 4])


In [19]:
meana= torch.mean(a, dim=-2)
print(meana, meana.shape)

tensor([[[-0.4688, -0.0633, -1.1198,  0.3554],
         [ 0.4214, -0.2453, -0.2500, -0.0615]]]) torch.Size([1, 2, 4])


In [20]:
z_score = meana/stda
print(z_score, z_score.shape)

tensor([[[-0.6607, -0.0740, -0.7300,  0.4835],
         [ 0.2882, -0.1609, -0.2241, -0.2607]]]) torch.Size([1, 2, 4])


In [16]:
torch.std(torch.tensor([-0.9570, -0.7945, 0.3452]))

tensor(0.7096)

In [29]:
std = -1
std = std + 1e-10 if std >= 0 else std - 1e-10
std

-1.0000000001

In [2]:
class Std(nn.Module):
    def __init__(self, stride=10) -> None:
        super().__init__()
        self.stride = stride
    
    def forward(self, feature):
        B, L, D = feature.shape

        feature = feature.reshape(-1, self.stride, D)
        return torch.std(feature, dim=-2, unbiased=False).reshape(-1, int(L/self.stride), D)


class ZScore(nn.Module):
    def __init__(self, stride=10) -> None:
        super().__init__()
        self.stride = stride
    
    def forward(self, feature):
        B, L, D = feature.shape

        feature = feature.reshape(B, -1, self.stride, D)
        std = torch.std(feature, dim=-2, unbiased=False)
        mean = torch.mean(feature, dim=-2)
        
        # std = std + 1e-10 if std >= 0 else std - 1e-10
        z_score = mean / std

        return z_score


class Return(nn.Module):
    def __init__(self, stride=10) -> None:
        super().__init__()
        self.stride = stride

    def forward(self, feature):

        numerators = feature[:, (self.stride - 1)::self.stride, :]
        denominators = feature[:, 0::self.stride, :]
        
        return numerators / (denominators + 1e-10) - 1.0


class LinearDecay(nn.Module):
    def __init__(self, stride) -> None:
        super().__init__()
        self.stride = stride
        lineardecay = torch.linspace(1.0, self.stride, steps=self.stride)
        self.weights =  lineardecay / lineardecay.sum()
    
    def forward(self, feature):
        B, L, D = feature.shape
        feature = feature.reshape(B, -1, self.stride, D)
        weights = self.weights.unsqueeze(1).expand(self.stride, D)
        weighted_feature = feature * weights

        return torch.sum(weighted_feature, dim=-2)


In [5]:
a = torch.randn(2, 2, 3)
eps = torch.full_like(a, 1e-6)
print(a, eps)
eps[a < 0] = -1e-6
print(eps)

tensor([[[ 1.4015, -1.9670, -0.6055],
         [-0.5396, -0.3338, -1.0908]],

        [[-2.0646,  0.4022,  0.7826],
         [-1.6030, -1.1455,  0.2029]]]) tensor([[[1.0000e-06, 1.0000e-06, 1.0000e-06],
         [1.0000e-06, 1.0000e-06, 1.0000e-06]],

        [[1.0000e-06, 1.0000e-06, 1.0000e-06],
         [1.0000e-06, 1.0000e-06, 1.0000e-06]]])
tensor([[[ 1.0000e-06, -1.0000e-06, -1.0000e-06],
         [-1.0000e-06, -1.0000e-06, -1.0000e-06]],

        [[-1.0000e-06,  1.0000e-06,  1.0000e-06],
         [-1.0000e-06, -1.0000e-06,  1.0000e-06]]])


In [24]:
import tensorflow as tf
a = tf.ones([4, 4])
mask_lower = tf.linalg.band_part(a, -1, 0)
print(mask_lower)
mask_diag = tf.linalg.band_part(a, 0, 0)
print(mask_diag)
mask = tf.cast(mask_lower - mask_diag, dtype=tf.bool)
print(mask)


tf.Tensor(
[[1. 0. 0. 0.]
 [1. 1. 0. 0.]
 [1. 1. 1. 0.]
 [1. 1. 1. 1.]], shape=(4, 4), dtype=float32)
tf.Tensor(
[[1. 0. 0. 0.]
 [0. 1. 0. 0.]
 [0. 0. 1. 0.]
 [0. 0. 0. 1.]], shape=(4, 4), dtype=float32)
tf.Tensor(
[[False False False False]
 [ True False False False]
 [ True  True False False]
 [ True  True  True False]], shape=(4, 4), dtype=bool)


In [10]:
class CovarianceTorch(nn.Module):
    def __init__(self, stride) -> None:
        super().__init__()
        self.stride = stride
        self.intermediate_shape = None
        self.out_shape = None
        self.lower_mask = None
        self.avg_pool2d = nn.AvgPool2d(kernel_size=(self.stride, 1), stride=(self.stride, 1))
    
    def forward(self, feature):
        B, L, D = feature.shape
        self.intermediate_shape = (-1, self.stride, D)
        output_features = int(D * (D - 1) / 2)
        self.out_shape = (-1, int(L/self.stride), output_features)
        self.lower_mask = torch.zeros(D, D, dtype=torch.int32)
        for i in range(D):
            self.lower_mask[i+1:, i] = 1
        
        means = self.avg_pool2d(feature[:, None, :, :]).squeeze(dim=1)
        means_brodcast = torch.repeat_interleave(means, repeats=self.stride, dim=1)
        means_substracted = torch.subtract(feature, means_brodcast)
        means_substracted = means_substracted.reshape(self.intermediate_shape)
        
        covariance_matrix = torch.einsum("ijk, ijm->ikm",
                                         means_substracted,
                                         means_substracted)

        covariance_matrix = covariance_matrix / (self.stride - 1)

        covariances = torch.masked_select(covariance_matrix, self.lower_mask.bool())
        covariances = covariances.reshape(self.out_shape)
        return covariances


In [11]:
class CorrelationTorch(nn.Module):
    def __init__(self, stride) -> None:
        super().__init__()
        self.stride = stride
        self.intermediate_shape = None
        self.out_shape = None
        self.lower_mask = None
        self.avg_pool2d = nn.AvgPool2d(kernel_size=(self.stride, 1), stride=(self.stride, 1))
    
    def forward(self, feature):
        B, L, D = feature.shape
        self.intermediate_shape = (-1, self.stride, D)
        output_features = int(D * (D - 1) / 2)
        self.out_shape = (-1, int(L/self.stride), output_features)
        self.lower_mask = torch.zeros(D, D, dtype=torch.int32)
        for i in range(D):
            self.lower_mask[i+1:, i] = 1
        
        means = self.avg_pool2d(feature[:, None, :, :]).squeeze(dim=1)
        means_brodcast = torch.repeat_interleave(means, repeats=self.stride, dim=1)
        means_substracted = torch.subtract(feature, means_brodcast)
        means_substracted = means_substracted.reshape(self.intermediate_shape)

        squared_diff = torch.square(means_substracted)
        mean_squared_error = torch.mean(squared_diff, dim=1)
        std = torch.sqrt(mean_squared_error)

        # get denominator of correlation matrix
        denominator_matrix = torch.einsum("ik,im->ikm", std, std)

        # compute covariance matrix
        covariance_matrix = torch.einsum("ijk,ijm->ikm",
                                       means_substracted,
                                       means_substracted)
        covariance_matrix = covariance_matrix / self.stride

        covariances = torch.masked_select(covariance_matrix, self.lower_mask.bool())
        denominators = torch.masked_select(denominator_matrix, self.lower_mask.bool())
        print(denominators.shape)
        correlations = torch.div(covariances, denominators)
        correlations = torch.reshape(correlations, self.out_shape)

        return correlations

In [12]:
from alphanet import Covariance, Correlation

2022-12-16 21:53:35.489949: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-12-16 21:54:03.706257: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 8680 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 2080 Ti, pci bus id: 0000:1a:00.0, compute capability: 7.5
2022-12-16 21:54:03.710706: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:1 with 8680 MB memory:  -> device: 1, name: NVIDIA GeForce RTX 2080 Ti, pci bus id: 0000:1b:00.0, compute capability: 7.5
2022-12-16 21:54:03.714446: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/repli

In [13]:
from alphanet import Std as Std_tf
from alphanet import ZScore as ZScore_tf
from alphanet import LinearDecay as LD_tf
from alphanet import Return as Return_tf
from alphanet import FeatureExpansion as Fe_tf

In [14]:
class FeatureExpansion(nn.Module):
    def __init__(self, stride=10) -> None:
        super().__init__()
        self.stride = stride
        self.std = Std(stride=self.stride)
        self.z_score = ZScore(stride=self.stride)
        self.linear_decay = LinearDecay(stride=self.stride)
        self.return_rate = Return(stride=self.stride)
        self.covariance = CovarianceTorch(stride=self.stride)
        self.correlation = CorrelationTorch(stride=self.stride)
    
    def forward(self, inputs):
        std_output = self.std(inputs)
        z_score_output = self.z_score(inputs)
        decay_linear_output = self.linear_decay(inputs)
        return_output = self.return_rate(inputs)
        covariance_output = self.covariance(inputs)
        correlation_output = self.correlation(inputs)

        return torch.cat([std_output,
                           z_score_output,
                           decay_linear_output,
                           return_output,
                           covariance_output,
                           correlation_output], dim=2)




In [76]:
cov_tf = Fe_tf(stride=3)
cov_torch = FeatureExpansion(stride=3)
inputs = np.random.randn(2, 9, 4)
inputs_torch = torch.from_numpy(inputs)
inputs_tf = tf.convert_to_tensor(inputs)
# print(inputs_torch, inputs_tf)
out_torch = cov_torch(inputs_torch)
out_tf = cov_tf(inputs_tf)
print(out_torch.shape, out_tf.shape)
print(np.sum((out_torch.numpy()-out_tf.numpy()) < 1e-6))


torch.Size([36])
torch.Size([2, 3, 28]) (2, 3, 28)
168


In [101]:
out_torch[:, -1, :].shape

torch.Size([2, 28])

In [32]:
class AlphaNetV3(nn.Module):
    def __init__(self, feat_dim=6, hidden_dim=30, dropout=0.0, classification=False) -> None:
        super().__init__()
        self.expand_dim = feat_dim * (feat_dim + 3)
        self.expanded10 = FeatureExpansion(stride=10)
        self.expanded5 = FeatureExpansion(stride=5)
        # expanded return shape (B, L/strie, feature*(feature+3))
        self.bn10 = nn.BatchNorm1d(self.expand_dim)
        self.bn5 = nn.BatchNorm1d(self.expand_dim)

        self.recurrent10 = nn.LSTM(input_size=self.expand_dim, hidden_size=hidden_dim, num_layers=1, batch_first=True)
        self.recurrent5 = nn.LSTM(input_size=self.expand_dim, hidden_size=hidden_dim, num_layers=1, batch_first=True)

        self.bn10_2 = nn.BatchNorm1d(hidden_dim)
        self.bn5_2 = nn.BatchNorm1d(hidden_dim)
        self.dropout = nn.Dropout(dropout)

        self.outputs = nn.Linear(hidden_dim*2, 1)

    def forward(self, inputs):
        expanded10 = self.expanded10(inputs)
        expanded5 = self.expanded5(inputs)

        bn10 = self.bn10(expanded10.transpose(1, 2)).transpose(1, 2)
        bn5 = self.bn5(expanded5.transpose(1, 2)).transpose(1, 2)
        # print(bn10, bn10.shape)
        recurrent10 = self.recurrent10(bn10)[0][:, -1, :]
        recurrent5 = self.recurrent5(bn5)[0][:, -1, :]

        bn10_2 = self.bn10_2(recurrent10)
        bn5_2 = self.bn5_2(recurrent5)

        x = torch.cat([bn10_2, bn5_2], dim=1)
        x = self.dropout(x)
        out = self.outputs(x)

        return out


In [34]:
inputs = torch.randn(2, 20, 6)
model = AlphaNetV3()
model(inputs)

torch.Size([60])
torch.Size([120])
tensor([[[-0.1757,  0.0690, -1.0535, -1.4536, -0.7240,  0.9879,  1.3509,
          -0.8316, -0.8178,  0.4439,  1.2156,  0.1440,  1.2770, -1.6830,
          -0.7925,  0.5173,  1.6027,  0.0151, -0.7000,  0.5442,  0.9820,
           0.3634,  1.5944, -0.5031, -1.0896,  0.2037,  0.9649, -0.0992,
          -0.9767, -1.1217, -0.1709,  1.6549, -0.2318, -0.7693, -0.5284,
           1.3125, -0.4370, -1.4704,  0.4416, -0.9760,  0.4805,  0.9962,
           0.5723, -1.2114, -1.2009, -0.5613,  1.7185, -0.7275, -1.2350,
          -0.5464,  0.9692, -0.3728, -1.5407,  0.5254],
         [ 1.5729, -0.4672,  0.0611,  1.3714, -0.7917, -1.1797, -0.0388,
           1.4038,  1.4571,  1.2604, -0.9328,  0.9822,  0.5577,  0.5148,
           1.4304,  1.3701, -1.1115,  0.9413, -0.3044,  0.5908, -0.0651,
          -1.6221, -0.1641,  1.0474,  1.6292,  1.1884, -0.1945,  1.3802,
          -0.2186,  1.1210, -1.5678, -0.0720,  0.4893,  0.8101,  1.5577,
          -0.2214,  1.6217,  1.33

tensor([[-0.5684],
        [ 0.3275]], grad_fn=<AddmmBackward0>)

In [98]:
lstm = tfl.LSTM(units=20)
inputs = np.random.randn(5, 3, 10)
lstm(inputs)

<tf.Tensor: shape=(5, 20), dtype=float32, numpy=
array([[ 0.01708459,  0.26434952, -0.12316011,  0.10814931,  0.07383276,
        -0.05396454, -0.00098636,  0.00195859,  0.03648054,  0.28365523,
        -0.1930024 ,  0.32060552,  0.02023736,  0.13143007, -0.07389427,
         0.14996853,  0.16222863, -0.08826179,  0.01318278, -0.09181478],
       [ 0.18093297,  0.16049507, -0.0852266 ,  0.00625607,  0.02544768,
         0.3022971 , -0.10152863,  0.10304444,  0.2788311 ,  0.35982257,
        -0.0917467 , -0.15553007,  0.13317071,  0.1997195 , -0.08908498,
        -0.01060249,  0.25772685, -0.11017278,  0.01542373,  0.05410857],
       [-0.02126176, -0.04341477,  0.0188271 ,  0.0011003 , -0.24236318,
        -0.04193686,  0.08093652, -0.09374363,  0.06927538,  0.10974678,
        -0.15501896, -0.00609506, -0.13258281, -0.05655068, -0.43860185,
         0.06844763, -0.0306216 ,  0.15605572, -0.15652648,  0.3403069 ],
       [ 0.16131833,  0.14084297,  0.04065484, -0.05247473, -0.16985483,

In [26]:
recurrent10 = nn.LSTM(input_size=54, hidden_size=30, num_layers=1, batch_first=True)
inputs = torch.randn(2, 2, 54)
type(recurrent10(inputs))

tuple

In [99]:
rnn = nn.LSTM(10, 20, 2)
input = torch.randn(5, 3, 10)
h0 = torch.randn(2, 3, 20)
c0 = torch.randn(2, 3, 20)
output, (hn, cn) = rnn(input)
output.shape

torch.Size([5, 3, 20])

In [94]:
bn = nn.BatchNorm1d(28)
bn(out_torch.transpose(1, 2).to(torch.float32)).shape

torch.Size([2, 28, 3])

In [78]:
import tensorflow.keras.layers as tfl

In [83]:
inputs = np.random.randn(4, 3, 2)
inputs_torch = torch.from_numpy(inputs)
inputs_tf = tf.convert_to_tensor(inputs)
tf_bn = tfl.BatchNormalization()
print(inputs)
tf_bn(inputs_tf)


[[[-0.75983587  0.26407615]
  [-0.87564859 -1.71973162]
  [ 0.32594103  0.66999354]]

 [[ 1.5958551   0.57318646]
  [-0.88636529  1.89849946]
  [-1.75862873 -0.50104446]]

 [[-0.84355001 -0.53202374]
  [-0.26162904  0.71715561]
  [ 0.16159098  2.04752762]]

 [[ 1.11618056  0.11693788]
  [ 0.24538989 -2.32287951]
  [ 0.75911768  0.4338718 ]]]


<tf.Tensor: shape=(4, 3, 2), dtype=float32, numpy=
array([[[-0.7594562 ,  0.26394418],
        [-0.875211  , -1.7188723 ],
        [ 0.32577816,  0.6696587 ]],

       [[ 1.5950577 ,  0.57290006],
        [-0.88592243,  1.8975508 ],
        [-1.75775   , -0.5007941 ]],

       [[-0.84312856, -0.5317579 ],
        [-0.26149833,  0.7167973 ],
        [ 0.16151024,  2.0465045 ]],

       [[ 1.1156229 ,  0.11687946],
        [ 0.24526729, -2.321719  ],
        [ 0.75873834,  0.43365502]]], dtype=float32)>

In [88]:
a = torch.arange(10)
b = a.reshape(1, 2, 5)
print(b)
print(b.transpose(1, 2))

tensor([[[0, 1, 2, 3, 4],
         [5, 6, 7, 8, 9]]])
tensor([[[0, 5],
         [1, 6],
         [2, 7],
         [3, 8],
         [4, 9]]])
